Load two surfaces of size $3*N_{\phi}*N_{\theta}$, where $\phi$ denotes the polar angle and $\theta$ denotes the azimuthal angle.

To use the code, $N_{\theta}$ must be odd.

In [1]:
import scipy.io as sio
from ShapePackages.ComputeGeoShapeModSO3 import *

# Example 

mat_f= sio.loadmat('ShapeData/example_50_99.mat') 
f1 = torch.from_numpy(mat_f['f1']).float() # 3*50*99
f2 = torch.from_numpy(mat_f['f2']).float()

Calculate a geodesic in the space of unparametrized surfaces modulo rigid motions

In [2]:
%%time

T = 7
a, b, c, d = 1, 1/2, 1, 0

opts = {'Cmetric': (a, b, c, d),  # choices of the split metric
        'Tpts': T,  # the number of the time points
        'MaxDegHarmSurf': 7,  # the maximal degree of spherical harmonics for the space of parametrized surfaces
        'MaxDegVecFS2': 7,  # the maximal degree of spherical harmonics for the tangent vector fields on S2
#         'method': 'combined',  # the method to calculate geodesics: 'split (default)', 'combined'
#         'multires': True, # only works for the split method
        'maxiter': (10, 20) # (N0, N1) N0: the maximal number of iterations for the whole optimization process
                            #          N1: the maximal number of iterations for each of the first N0-1 optimizations
                            #        In the last optimization process 100 maximum iterations is used. The whole maximal
                            #        number of iterations will be (N0-1)*N1 + 100  
       }  

geo_f, EnergyAll0 = compute_geodesic_shape_main(f1, f2, **opts)

Wall time: 2min 47s


In [3]:
from ShapePackages.OneFormRieMetric import length_func_surf_Imm
length_func_surf_Imm(geo_f, a, b, c, d)

tensor(1.3765)

In [4]:
print('The number of iterations in the optimization process is', len(EnergyAll0),'and the final energy is', EnergyAll0[-1])

The number of iterations in the optimization process is 168 and the final energy is 1.897215485572815


In [5]:
# plot the energy 
import matplotlib.pyplot as plt
plt.plot(EnergyAll0)
plt.show()

<Figure size 640x480 with 1 Axes>

In [6]:
# plot the geodesic

idty = get_idty_S2(*f1.shape[-2:])

from mayavi import mlab
Gx, Gy = np.gradient(idty[2]) # gradients with respect to x and y
Grad = (Gx**2+Gy**2)**.5  # gradient magnitude  PHI, THETA
w = Grad/Grad.max()  

%gui qt

mlab.init_notebook('x3d',1000,500) # png & x3d
mlab.figure(1, size=(100,70), fgcolor=(1, 1, 1), bgcolor=(0.5, 0.5, 0.5))
mlab.clf()

# plot the geodesic
for i in range(T):
    s0 = mlab.mesh(geo_f[i, 0].numpy()+2*i, geo_f[i, 1].numpy(), geo_f[i, 2].numpy()-2,representation='wireframe',scalars=w)

mlab.view(azimuth=270, elevation=90)
mlab.show()
s0

Notebook initialized with x3d backend.
